In [2]:
import pandas as pd

from db.database import sync_session_factory
from db.queries.core import SyncCore as SC

#### Формирование DF из таблиц БД

In [3]:
def get_data_from_tables(table_names: list[str]) -> dict[str, pd.DataFrame]:
    res = {}
    for table_name in table_names:
        query = f"select * from {table_name}"
        with sync_session_factory() as session:
            df = pd.read_sql(query, session.connection())
        res[table_name] = df
    return res

In [4]:
TABLE_NAMES = SC.get_table_names()

In [5]:
dict_df = get_data_from_tables(TABLE_NAMES)

In [6]:
dict_df['game'].info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2160 entries, 0 to 2159
Data columns (total 15 columns):
 #   Column          Non-Null Count  Dtype         
---  ------          --------------  -----         
 0   game_id         2160 non-null   int64         
 1   season_game_id  2160 non-null   object        
 2   season_id       2160 non-null   object        
 3   left_team_id    2160 non-null   object        
 4   right_team_id   2160 non-null   object        
 5   game_status_id  2160 non-null   int64         
 6   tour_number     2160 non-null   int64         
 7   start_date      2160 non-null   object        
 8   start_time      2160 non-null   object        
 9   min             0 non-null      object        
 10  plus_min        0 non-null      object        
 11  created_at      2160 non-null   datetime64[ns]
 12  updated_at      2160 non-null   datetime64[ns]
 13  left_coach_id   2160 non-null   object        
 14  right_coach_id  2160 non-null   object        
dtypes: d

#### Моделирование матчей

In [86]:
def add_time_event(time_events: set, 
                   min_column_name: str, 
                   plus_min_column_name: str, 
                   df: pd.DataFrame):
    for _, row in df.iterrows():
        if not pd.isna(row[min_column_name]):
            time_events.add((row[min_column_name], row[plus_min_column_name]))
    

def add_game_row(df_game: pd.DataFrame, 
                 df_referee_game: pd.DataFrame,
                 df_goal: pd.DataFrame,
                 df_goal_type: pd.DataFrame,
                 df_lineup: pd.DataFrame,
                 df_penalty: pd.DataFrame) -> pd.DataFrame:
    """Функция, добавляющая строки по количеству записей из таблиц goal, lineup, penalty, для симуляции матча"""
    
    res_df = pd.DataFrame(columns=['season_id',
                                   'game_id',
                                   'left_team_id',
                                   'right_team_id',
                                   'tour_number',
                                   'min',
                                   'plus_min',
                                   'left_coach_id',
                                   'right_coach_id',
                                   'referee_id',
                                   'left_num_v',
                                   'left_num_z',
                                   'left_num_p',
                                   'left_num_n',
                                   'left_num_u',
                                   'right_num_v',
                                   'right_num_z',
                                   'right_num_p',
                                   'right_num_n',
                                   'right_num_u',
                                   'left_num_y',
                                   'left_num_y2r',
                                   'right_num_y',
                                   'right_num_y2r',
                                   'right_num_goal_g',
                                   'right_num_goal_p',
                                   'right_num_goal_a',
                                   'left_num_goal_g',
                                   'left_num_goal_p',
                                   'left_num_goal_a',
                                   'left_total_transfer_value',
                                   'right_total_transfer_value',
                                   'left_avg_transfer_value',
                                   'right_avg_transfer_value',
                                   'left_goal_score',
                                   'right_goal_score',
                                   'left_avg_time_player_in_game',
                                   'right_avg_time_player_in_game',
                                   'left_right_transfer_value_div',
                                   'right_left_transfer_value_div'
                                   ])  
    df_game = df_game.join(df_referee_game.set_index('game_id'), 'game_id')
    
    for _, row_game in df_game.iterrows():        
        
        if row_game['game_status_id'] != 1: continue # обрабатываем только завершенные игры 
        
        time_events = set() # время возникновения какого либо события в матче
        
        season_id = row_game['season_id']
        game_id = row_game['game_id']
        left_team_id = row_game['left_team_id']
        right_team_id = row_game['right_team_id']
        tour_number = row_game['tour_number']
        left_coach_id = row_game['left_coach_id']
        right_coach_id = row_game['right_coach_id']
        referee_id = row_game['referee_id']
        
        game_player_stat_amplua = SC.get_lineup_player_stat_for_game(game_id)
        
        
        left_goals_df = df_goal.loc[(df_goal['game_id']==game_id) & (df_goal['team_id']==left_team_id)]
        left_goals_df['plus_min'] = left_goals_df['plus_min'].fillna(0)
        left_goals_df.sort_values(by=['min', 'plus_min'], ascending=[True, True])
        left_goals_df = left_goals_df.join(df_goal_type.set_index('goal_type_id'), 'goal_type_id')
        add_time_event(time_events, 'min', 'plus_min', left_goals_df)     
        
        left_penalty_df = df_penalty.loc[(df_penalty['game_id']==game_id) & (df_penalty['team_id']==left_team_id)]
        left_penalty_df = left_penalty_df.join(dict_df['penalty_type'].set_index('penalty_type_id'), 'penalty_type_id')
        left_penalty_df['plus_min'] = left_penalty_df['plus_min'].fillna(0)
        left_penalty_df.sort_values(by=['min', 'plus_min'], ascending=[True, True])
        add_time_event(time_events, 'min', 'plus_min', left_penalty_df)
        
        left_lineup_df = df_lineup.loc[(df_lineup['game_id']==game_id) & (df_lineup['team_id']==left_team_id)]
        left_lineup_df['min_in'] = left_lineup_df['min_in'].fillna(0)
        left_lineup_df['plus_min_in'] = left_lineup_df['plus_min_in'].fillna(0)
        mask_left_lineup = left_lineup_df['min_out'].notna()
        left_lineup_df.loc[mask_left_lineup, 'plus_min_out'] = (
            left_lineup_df.loc[mask_left_lineup, 'plus_min_out'].fillna(0)
        )
        left_lineup_df = left_lineup_df.join(game_player_stat_amplua.set_index('player_id'), 'player_id')
        #назначим время выхода из игры игрокам, которые получили наказания: yellow2 или red
        for __, left_penalty_row in left_penalty_df.loc[(left_penalty_df['name']=='yellow2') | (left_penalty_df['name']=='red')].iterrows():
            player_penalty_id = left_penalty_row['player_id']
            
            mask = left_lineup_df['player_id'] == player_penalty_id
            left_lineup_df.loc[mask, ['min_out', 'plus_min_out']] = [
                left_penalty_row['min'],
                left_penalty_row['plus_min']
            ]
        add_time_event(time_events, 'min_out', 'plus_min_out', left_lineup_df)
        
        
        right_goals_df = df_goal.loc[(df_goal['game_id']==game_id) & (df_goal['team_id']==right_team_id)]
        right_goals_df['plus_min'] = right_goals_df['plus_min'].fillna(0)
        right_goals_df.sort_values(by=['min', 'plus_min'], ascending=[True, True])
        right_goals_df = right_goals_df.join(df_goal_type.set_index('goal_type_id'), 'goal_type_id')
        add_time_event(time_events, 'min', 'plus_min', right_goals_df) 
        
        right_penalty_df = df_penalty.loc[(df_penalty['game_id']==game_id) & (df_penalty['team_id']==right_team_id)]
        right_penalty_df = right_penalty_df.join(dict_df['penalty_type'].set_index('penalty_type_id'), 'penalty_type_id')
        right_penalty_df['plus_min'] = right_penalty_df['plus_min'].fillna(0)
        right_penalty_df.sort_values(by=['min', 'plus_min'], ascending=[True, True])
        add_time_event(time_events, 'min', 'plus_min', right_penalty_df) 
        
        right_lineup_df = df_lineup.loc[(df_lineup['game_id']==game_id) & (df_lineup['team_id']==right_team_id)]
        right_lineup_df['min_in'] = right_lineup_df['min_in'].fillna(0)
        right_lineup_df['plus_min_in'] = right_lineup_df['plus_min_in'].fillna(0)
        mask_right_lineup = right_lineup_df['min_out'].notna()
        right_lineup_df.loc[mask_right_lineup, 'plus_min_out'] = (
            right_lineup_df.loc[mask_right_lineup, 'plus_min_out'].fillna(0)
        )
        right_lineup_df = right_lineup_df.join(game_player_stat_amplua.set_index('player_id'), 'player_id')
        #назначим время выхода из игры игрокам, которые получили наказания: yellow2 или red
        for _, right_penalty_row in right_penalty_df.loc[(right_penalty_df['name']=='yellow2') | (right_penalty_df['name']=='red')].iterrows():
            player_penalty_id = right_penalty_row['player_id']
            
            mask = right_lineup_df['player_id'] == player_penalty_id
            right_lineup_df.loc[mask, ['min_out', 'plus_min_out']] = [
                right_penalty_row['min'],
                right_penalty_row['plus_min']
            ]
        add_time_event(time_events, 'min_out', 'plus_min_out', right_lineup_df)
        
        
        for time_event in time_events:
            min = time_event[0]
            plus_min = time_event[1]
            
            left_goal_score = len(left_goals_df.loc[(left_goals_df['min'] <= min) & (left_goals_df['plus_min'] <= plus_min)])
            right_goal_score = len(right_goals_df.loc[(right_goals_df['min'] <= min) & (right_goals_df['plus_min'] <= plus_min)])
            
            left_num_y = len(left_penalty_df.loc[(left_penalty_df['min'] <= min) & (left_penalty_df['plus_min'] <= plus_min) & (left_penalty_df['name'] == 'yellow')])
            left_num_y2r = len(left_penalty_df.loc[(left_penalty_df['min'] <= min) & (left_penalty_df['plus_min'] <= plus_min) & ((left_penalty_df['name'] == 'yellow2') | (left_penalty_df['name'] == 'red'))])
            
            right_num_y = len(right_penalty_df.loc[(right_penalty_df['min'] <= min) & (right_penalty_df['plus_min'] <= plus_min) & (right_penalty_df['name'] == 'yellow')])
            right_num_y2r = len(right_penalty_df.loc[(right_penalty_df['min'] <= min) & (right_penalty_df['plus_min'] <= plus_min) & ((right_penalty_df['name'] == 'yellow2') | (right_penalty_df['name'] == 'red'))])
            
            cur_left_lineup = left_lineup_df.loc[
                (left_lineup_df['min_in'] <= min) & 
                (left_lineup_df['plus_min_in'] <= plus_min) &
                (
                    ((pd.isna(left_lineup_df['min_out'])) | (pd.isna(left_lineup_df['plus_min_out']))) |
                    ((left_lineup_df['min_out'] > min) | ((left_lineup_df['min_out'] == min) & (left_lineup_df['plus_min_out'] > plus_min)))
                )
                ]
            left_num_v = len(cur_left_lineup.loc[cur_left_lineup['name'] == 'вратарь'])
            left_num_z = len(cur_left_lineup.loc[cur_left_lineup['name'] == 'защитник'])
            left_num_p = len(cur_left_lineup.loc[cur_left_lineup['name'] == 'полузащитник'])
            left_num_n = len(cur_left_lineup.loc[cur_left_lineup['name'] == 'нападающий'])
            left_num_u = len(cur_left_lineup.loc[cur_left_lineup['name'] == 'неизвестно'])
            left_num_goal_g = len(left_goals_df.loc[(left_goals_df['min'] <= min) & (left_goals_df['plus_min'] <= plus_min) & (left_goals_df['name'] == 'гол')])
            left_num_goal_p = len(left_goals_df.loc[(left_goals_df['min'] <= min) & (left_goals_df['plus_min'] <= plus_min) & (left_goals_df['name'] == 'пенальти')])
            left_num_goal_a = len(left_goals_df.loc[(left_goals_df['min'] <= min) & (left_goals_df['plus_min'] <= plus_min) & (left_goals_df['name'] == 'автогол')])
            left_total_transfer_value = cur_left_lineup['transfer_value'].sum()
            left_avg_transfer_value = cur_left_lineup['transfer_value'].mean()
            left_avg_time_player_in_game = cur_left_lineup.apply(lambda row: min - row['min_in'], axis=1).mean()
            
            cur_right_lineup = right_lineup_df.loc[
                (right_lineup_df['min_in'] <= min) & 
                (right_lineup_df['plus_min_in'] <= plus_min) &
                (
                    ((pd.isna(right_lineup_df['min_out'])) | (pd.isna(right_lineup_df['plus_min_out']))) |
                    ((right_lineup_df['min_out'] > min) | ((right_lineup_df['min_out'] == min) & (right_lineup_df['plus_min_out'] > plus_min)))
                )
                ]
            
            right_num_v = len(cur_right_lineup.loc[cur_right_lineup['name'] == 'вратарь'])
            right_num_z = len(cur_right_lineup.loc[cur_right_lineup['name'] == 'защитник'])
            right_num_p = len(cur_right_lineup.loc[cur_right_lineup['name'] == 'полузащитник'])
            right_num_n = len(cur_right_lineup.loc[cur_right_lineup['name'] == 'нападающий'])
            right_num_u = len(cur_right_lineup.loc[cur_right_lineup['name'] == 'неизвестно'])
            right_num_goal_g = len(right_goals_df.loc[(right_goals_df['min'] <= min) & (right_goals_df['plus_min'] <= plus_min) & (right_goals_df['name'] == 'гол')])
            right_num_goal_p = len(right_goals_df.loc[(right_goals_df['min'] <= min) & (right_goals_df['plus_min'] <= plus_min) & (right_goals_df['name'] == 'пенальти')])
            right_num_goal_a = len(right_goals_df.loc[(right_goals_df['min'] <= min) & (right_goals_df['plus_min'] <= plus_min) & (right_goals_df['name'] == 'автогол')])
            right_total_transfer_value = cur_right_lineup['transfer_value'].sum()
            right_avg_transfer_value = cur_right_lineup['transfer_value'].mean()
            right_avg_time_player_in_game = cur_right_lineup.apply(lambda row: min - row['min_in'], axis=1).mean()            
            
            
            left_right_transfer_value_div = left_total_transfer_value / right_total_transfer_value
            right_left_transfer_value_div = right_total_transfer_value / left_total_transfer_value
            
            new_row = {
                'season_id':[season_id],
                'game_id':[game_id],
                'left_team_id':[left_team_id],
                'right_team_id':[right_team_id],
                'tour_number':[tour_number],
                'min':[min],
                'plus_min':[plus_min],
                'left_coach_id':[left_coach_id],
                'right_coach_id':[right_coach_id],
                'referee_id':[referee_id],
                'left_num_v':[left_num_v],
                'left_num_z':[left_num_z],
                'left_num_p':[left_num_p],
                'left_num_n':[left_num_n],
                'left_num_u':[left_num_u],
                'right_num_v':[right_num_v],
                'right_num_z':[right_num_z],
                'right_num_p':[right_num_p],
                'right_num_n':[right_num_n],
                'right_num_u':[right_num_u],
                'left_num_y':[left_num_y],
                'left_num_y2r':[left_num_y2r],
                'right_num_y':[right_num_y],
                'right_num_y2r':[right_num_y2r],
                'right_num_goal_g':[right_num_goal_g],
                'right_num_goal_p':[right_num_goal_p],
                'right_num_goal_a':[right_num_goal_a],
                'left_num_goal_g':[left_num_goal_g],
                'left_num_goal_p':[left_num_goal_p],
                'left_num_goal_a':[left_num_goal_a],
                'left_total_transfer_value':[left_total_transfer_value],
                'right_total_transfer_value':[right_total_transfer_value],
                'left_avg_transfer_value':[left_avg_transfer_value],
                'right_avg_transfer_value':[right_avg_transfer_value],
                'left_goal_score':[left_goal_score],
                'right_goal_score':[right_goal_score],
                'left_avg_time_player_in_game':[left_avg_time_player_in_game],
                'right_avg_time_player_in_game':[right_avg_time_player_in_game],
                'left_right_transfer_value_div':[left_right_transfer_value_div],
                'right_left_transfer_value_div':[right_left_transfer_value_div],
            }
            new_row_df = pd.DataFrame(new_row)

            res_df = pd.concat([res_df, new_row_df], ignore_index=True)
        
    return res_df
   

In [87]:
add_game_row(df_game=dict_df['game'],
             df_referee_game=dict_df['referee_game'],
             df_goal=dict_df['goal'],
             df_goal_type=dict_df['goal_type'],
             df_lineup=dict_df['lineup'],
             df_penalty=dict_df['penalty']).to_csv('test_123.csv', index=False)

C:\Users\vlaxd\AppData\Local\Temp\ipykernel_21172\1156982315.py:92: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  left_lineup_df['min_in'] = left_lineup_df['min_in'].fillna(0)
C:\Users\vlaxd\AppData\Local\Temp\ipykernel_21172\1156982315.py:93: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  left_lineup_df['plus_min_in'] = left_lineup_df['plus_min_in'].fillna(0)
C:\Users\vlaxd\AppData\Local\Temp\ipykernel_21172\1156982315.py:124: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 

#### Подготовка данных к анализу

In [70]:
df = pd.read_csv('test_123.csv')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 25893 entries, 0 to 25892
Data columns (total 40 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   season_id                      25893 non-null  int64  
 1   game_id                        25893 non-null  int64  
 2   left_team_id                   25893 non-null  object 
 3   right_team_id                  25893 non-null  object 
 4   tour_number                    25893 non-null  int64  
 5   min                            25893 non-null  float64
 6   plus_min                       25893 non-null  float64
 7   left_coach_id                  25893 non-null  int64  
 8   right_coach_id                 25893 non-null  int64  
 9   referee_id                     25848 non-null  float64
 10  left_num_v                     25893 non-null  int64  
 11  left_num_z                     25893 non-null  int64  
 12  left_num_p                     25893 non-null 

In [42]:
pd.set_option('display.max_columns', None)

In [71]:
sorted_df = df.sort_values(by=['game_id', 'min', 'plus_min'], ignore_index=True)
sorted_df.head()

season_id  game_id left_team_id   right_team_id  tour_number   min  \
0       1768      728   5-fk-zenit  3-fk-lokomotiv            1  36.0   
1       1768      728   5-fk-zenit  3-fk-lokomotiv            1  51.0   
2       1768      728   5-fk-zenit  3-fk-lokomotiv            1  59.0   
3       1768      728   5-fk-zenit  3-fk-lokomotiv            1  63.0   
4       1768      728   5-fk-zenit  3-fk-lokomotiv            1  66.0   

   plus_min  left_coach_id  right_coach_id  referee_id  left_num_v  \
0       0.0           8935            1709       416.0           1   
1       0.0           8935            1709       416.0           1   
2       0.0           8935            1709       416.0           1   
3       0.0           8935            1709       416.0           1   
4       0.0           8935            1709       416.0           1   

   left_num_z  left_num_p  left_num_n  left_num_u  right_num_v  right_num_z  \
0           3           4           2           1            1            3   
1           3           4           2           1            1            3   
2           3           3           2           2            1            3   
3           3           4           1           2            1            3   
4           3           4           1           2            1            3   

   right_num_p  right_num_n  right_num_u  left_num_y  left_num_y2r  \
0            6            1            0           0             0   
1            6            1            0           0             0   
2            6            1            0           0             0   
3            6            1            0           0             0   
4            7            0            0           0             0   

   right_num_y  right_num_y2r  right_num_goal_g  right_num_goal_p  \
0            1              0                 0                 0   
1            2              0                 0                 0   
2            2              0                 0                 0   
3            2              0                 0                 0   
4            2              0                 0                 0   

   right_num_goal_a  left_num_goal_g  left_num_goal_p  left_num_goal_a  \
0                 0                0                0                0   
1                 0                0                0                0   
2                 0                0                0                0   
3                 0                0                0                0   
4                 0                0                0                0   

   left_total_transfer_value  right_total_transfer_value  \
0                 52000000.0                  39800000.0   
1                 52000000.0                  39800000.0   
2                 49000000.0                  39800000.0   
3                 51000000.0                  39800000.0   
4                 51000000.0                  40800000.0   

   left_avg_transfer_value  right_avg_transfer_value  left_goal_score  \
0             4.727273e+06              3.618182e+06                0   
1             4.727273e+06              3.618182e+06                0   
2             4.454545e+06              3.618182e+06                0   
3             4.636364e+06              3.618182e+06                0   
4             4.636364e+06              3.709091e+06                0   

   right_goal_score  left_avg_time_player_in_game  \
0                 0                     36.000000   
1                 0                     51.000000   
2                 0                     53.636364   
3                 0                     51.909091   
4                 0                     54.909091   

   right_avg_time_player_in_game  left_right_transfer_value_div  \
0                           36.0                       1.306533   
1                           51.0                       1.306533   
2                           59.0                       1.231156   


Закодируем столбцы left_team_id и right_team_id

In [72]:
# добавить team_code

from sklearn.preprocessing import LabelEncoder

le_team = LabelEncoder()
le_team.fit_transform(SC.get_team_id_list())

sorted_df['left_team_id'] = le_team.transform(sorted_df['left_team_id'])
sorted_df['right_team_id'] = le_team.transform(sorted_df['right_team_id'])

In [73]:
sorted_df.head()

season_id  game_id  left_team_id  right_team_id  tour_number   min  \
0       1768      728            15             11            1  36.0   
1       1768      728            15             11            1  51.0   
2       1768      728            15             11            1  59.0   
3       1768      728            15             11            1  63.0   
4       1768      728            15             11            1  66.0   

   plus_min  left_coach_id  right_coach_id  referee_id  left_num_v  \
0       0.0           8935            1709       416.0           1   
1       0.0           8935            1709       416.0           1   
2       0.0           8935            1709       416.0           1   
3       0.0           8935            1709       416.0           1   
4       0.0           8935            1709       416.0           1   

   left_num_z  left_num_p  left_num_n  left_num_u  right_num_v  right_num_z  \
0           3           4           2           1            1            3   
1           3           4           2           1            1            3   
2           3           3           2           2            1            3   
3           3           4           1           2            1            3   
4           3           4           1           2            1            3   

   right_num_p  right_num_n  right_num_u  left_num_y  left_num_y2r  \
0            6            1            0           0             0   
1            6            1            0           0             0   
2            6            1            0           0             0   
3            6            1            0           0             0   
4            7            0            0           0             0   

   right_num_y  right_num_y2r  right_num_goal_g  right_num_goal_p  \
0            1              0                 0                 0   
1            2              0                 0                 0   
2            2              0                 0                 0   
3            2              0                 0                 0   
4            2              0                 0                 0   

   right_num_goal_a  left_num_goal_g  left_num_goal_p  left_num_goal_a  \
0                 0                0                0                0   
1                 0                0                0                0   
2                 0                0                0                0   
3                 0                0                0                0   
4                 0                0                0                0   

   left_total_transfer_value  right_total_transfer_value  \
0                 52000000.0                  39800000.0   
1                 52000000.0                  39800000.0   
2                 49000000.0                  39800000.0   
3                 51000000.0                  39800000.0   
4                 51000000.0                  40800000.0   

   left_avg_transfer_value  right_avg_transfer_value  left_goal_score  \
0             4.727273e+06              3.618182e+06                0   
1             4.727273e+06              3.618182e+06                0   
2             4.454545e+06              3.618182e+06                0   
3             4.636364e+06              3.618182e+06                0   
4             4.636364e+06              3.709091e+06                0   

   right_goal_score  left_avg_time_player_in_game  \
0                 0                     36.000000   
1                 0                     51.000000   
2                 0                     53.636364   
3                 0                     51.909091   
4                 0                     54.909091   

   right_avg_time_player_in_game  left_right_transfer_value_div  \
0                           36.0                       1.306533   
1                           51.0                       1.306533   
2                           59.0                       1.231156   


Добавим столбец факторный признак res_event - отражающий исход матча в пределах события и целевой признак res - отражающий исход матча вцелом:
- 0 - ничья
- 1 - победа левой команды
- 2 - победа правой команды

In [80]:
def calculate_res_event(l_score: int, r_score: int) -> int:
    if l_score > r_score: return 1
    elif l_score < r_score: return 2
    else: return 0
    
   
def calculate_res(game_id: int) -> int:
    l_score = sorted_df.loc[sorted_df['game_id']==game_id]['left_goal_score'].max()
    r_score = sorted_df.loc[sorted_df['game_id']==game_id]['right_goal_score'].max()
    return calculate_res_event(l_score, r_score)

sorted_df['res_event'] = sorted_df.apply(
    lambda row: calculate_res_event(row['left_goal_score'], row['right_goal_score']),
    axis=1)

sorted_df['res'] = sorted_df.apply(
    lambda row: calculate_res(row['game_id']),
    axis=1
)

In [84]:
sorted_df.tail()

season_id  game_id  left_team_id  right_team_id  tour_number   min  \
25888       5980     2855             7             16           26  79.0   
25889       5980     2855             7             16           26  88.0   
25890       5980     2855             7             16           26  89.0   
25891       5980     2855             7             16           26  90.0   
25892       5980     2855             7             16           26  90.0   

       plus_min  left_coach_id  right_coach_id  referee_id  left_num_v  \
25888       0.0           6442            6442     11888.0           1   
25889       0.0           6442            6442     11888.0           1   
25890       0.0           6442            6442     11888.0           1   
25891       4.0           6442            6442     11888.0           1   
25892       5.0           6442            6442     11888.0           1   

       left_num_z  left_num_p  left_num_n  left_num_u  right_num_v  \
25888           4           3           2           0            1   
25889           4           3           2           0            1   
25890           4           3           2           0            1   
25891           4           3           2           0            1   
25892           4           4           2           0            1   

       right_num_z  right_num_p  right_num_n  right_num_u  left_num_y  \
25888            4            2            2            0           1   
25889            4            2            2            0           2   
25890            4            2            2            0           2   
25891            5            2            2            0           2   
25892            5            2            2            0           3   

       left_num_y2r  right_num_y  right_num_y2r  right_num_goal_g  \
25888             0            1              0                 1   
25889             0            1              0                 1   
25890             0            1              0                 1   
25891             0            2              0                 1   
25892             0            2              0                 1   

       right_num_goal_p  right_num_goal_a  left_num_goal_g  left_num_goal_p  \
25888                 0                 0                1                0   
25889                 0                 0                1                0   
25890                 0                 0                2                0   
25891                 0                 0                2                0   
25892                 0                 0                2                0   

       left_num_goal_a  left_total_transfer_value  right_total_transfer_value  \
25888                0                 12000000.0                   5150000.0   
25889                0                 12000000.0                   5150000.0   
25890                0                 12000000.0                   5150000.0   
25891                0                 12000000.0                   5150000.0   
25892                0                 12900000.0                   5150000.0   

       left_avg_transfer_value  right_avg_transfer_value  left_goal_score  \
25888             1.200000e+06             572222.222222                1   
25889             1.200000e+06             572222.222222                1   
25890             1.200000e+06             572222.222222                2   
25891             1.200000e+06             515000.000000                2   
25892             1.172727e+06             515000.000000                2   

       right_goal_score  left_avg_time_player_in_game  \
25888                 1                     59.200000   
25889                 1                     68.200000   
25890                 1                     69.200000   
25891                 1                     70.200000   
25892                 1                     67.909091   

       right_avg_time_player_in_game  left_right_transfe

Пропуски в данных к общему количеству записей

In [85]:
missing_ratio = (sorted_df.isna().sum() / len(sorted_df)).loc[lambda x: x > 0]
missing_ratio

referee_id    0.001738
dtype: float64

In [86]:
missing_counts = sorted_df.isna().sum().loc[lambda x: x > 0]
missing_counts

referee_id    45
dtype: int64

In [87]:
missing_game_id = set(sorted_df['game_id'].loc[pd.isna(sorted_df['referee_id'])])
missing_game_id

{1467, 1492, 1493, 1548}

In [88]:
for i in missing_game_id:
    drop_index_game = sorted_df[sorted_df['game_id'] == i].index
    sorted_df.drop(drop_index_game, inplace=True)

In [89]:
missing_ratio = (sorted_df.isna().sum() / len(sorted_df)).loc[lambda x: x > 0]
missing_ratio

Series([], dtype: float64)

#### Предварительный анализ данных

In [90]:
def beautify_float(value):
  """Эта функция берет на вход вещественное число
  и преобразует его в строку вида 'целая часть.2 разряда дробной части'"""
  return "{:.2f}".format(value)

In [91]:
sorted_df.describe().applymap(beautify_float)

c:\Users\vlaxd\OneDrive\Рабочий стол\4_course\вкр_2024_2025\degree-work-2024-2025\venv\Lib\site-packages\pandas\core\nanops.py:1016: RuntimeWarning: invalid value encountered in subtract
  sqr = _ensure_numeric((avg - values) ** 2)
c:\Users\vlaxd\OneDrive\Рабочий стол\4_course\вкр_2024_2025\degree-work-2024-2025\venv\Lib\site-packages\pandas\core\nanops.py:1016: RuntimeWarning: invalid value encountered in subtract
  sqr = _ensure_numeric((avg - values) ** 2)
C:\Users\vlaxd\AppData\Local\Temp\ipykernel_17504\3116729034.py:1: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  sorted_df.describe().applymap(beautify_float)


season_id   game_id left_team_id right_team_id tour_number       min  \
count  25848.00  25848.00     25848.00      25848.00    25848.00  25848.00   
mean    3850.29   1819.70        15.19         15.12       15.37     61.43   
std     1376.23    599.61         8.00          8.00        8.56     23.06   
min     1768.00    728.00         0.00          0.00        1.00      0.00   
25%     2599.00   1319.00         8.00          8.00        8.00     46.00   
50%     3953.00   1834.00        15.00         15.00       15.00     66.00   
75%     4987.00   2323.00        22.00         22.00       23.00     80.25   
max     5980.00   2855.00        29.00         29.00       30.00     90.00   

       plus_min left_coach_id right_coach_id referee_id left_num_v left_num_z  \
count  25848.00      25848.00       25848.00   25848.00   25848.00   25848.00   
mean       0.26      27577.34       26483.88    1450.75       0.98       3.84   
std        1.02      60441.67       58749.34    2577.68       0.17       1.04   
min        0.00         14.00          14.00       3.00       0.00       0.00   
25%        0.00       3953.00        3953.00     398.00       1.00       3.00   
50%        0.00       5135.00        4989.00     707.00       1.00       4.00   
75%        0.00      10386.00        8876.00    1137.00       1.00       4.00   
max       16.00     450457.00      450457.00   15584.00       2.00       8.00   

      left_num_p left_num_n left_num_u right_num_v right_num_z right_num_p  \
count   25848.00   25848.00   25848.00    25848.00    25848.00    25848.00   
mean        3.96       1.74       0.57        0.98        3.87        3.98   
std         1.35       0.94       1.12        0.17        1.07        1.33   
min         0.00       0.00       0.00        0.00        0.00        0.00   
25%         3.00       1.00       0.00        1.00        3.00        3.00   
50%         4.00       2.00       0.00        1.00        4.00        4.00   
75%         5.00       2.00       1.00        1.00        5.00        5.00   
max         9.00       6.00      10.00        2.00        8.00        9.00   

      right_num_n right_num_u left_num_y left_num_y2r right_num_y  \
count    25848.00    25848.00   25848.00     25848.00    25848.00   
mean         1.67        0.58       1.27         0.06        1.46   
std          0.93        1.11       1.19         0.24        1.27   
min          0.00        0.00       0.00         0.00        0.00   
25%          1.00        0.00       0.00         0.00        0.00   
50%          2.00        0.00       1.00         0.00        1.00   
75%          2.00        1.00       2.00         0.00        2.00   
max          5.00        9.00       9.00         2.00        8.00   

      right_num_y2r right_num_goal_g right_num_goal_p right_num_goal_a  \
count      25848.00         25848.00         25848.00         25848.00   
mean           0.08             0.65             0.07             0.02   
std            0.29             0.86             0.27             0.13   
min            0.00             0.00             0.00             0.00   
25%            0.00             0.00             0.00             0.00   
50%            0.00             0.00             0.00             0.00   
75%            0.00             1.00             0.00             0.00   
max            3.00             7.00             3.00             1.00   

      left_num_goal_g left_num_goal_p left_num_goal_a  \
count        25848.00        25848.00        25848.00   
mean             0.81            0.11            0.03   
std              0.98            0.33            0.17   
min              0.00            0.00            0.00   
25%              0.00            0.00            0.00   
50%              1.00            0.00            0.00   
75%              1.00            0.00            0.00   
max              8.00            3.00            1.00   

      left_total_transfer_value right_total_transfer_value  \
count

Заменим значения inf в столбцах left_right_transfer_value_div и right_left_transfer_value_div на максимальное значение int

In [92]:
import numpy as np

sorted_df = sorted_df.replace([-np.inf, np.inf], [-9999, 9999])
sorted_df.describe().applymap(beautify_float)

C:\Users\vlaxd\AppData\Local\Temp\ipykernel_17504\1941608419.py:4: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  sorted_df.describe().applymap(beautify_float)


season_id   game_id left_team_id right_team_id tour_number       min  \
count  25848.00  25848.00     25848.00      25848.00    25848.00  25848.00   
mean    3850.29   1819.70        15.19         15.12       15.37     61.43   
std     1376.23    599.61         8.00          8.00        8.56     23.06   
min     1768.00    728.00         0.00          0.00        1.00      0.00   
25%     2599.00   1319.00         8.00          8.00        8.00     46.00   
50%     3953.00   1834.00        15.00         15.00       15.00     66.00   
75%     4987.00   2323.00        22.00         22.00       23.00     80.25   
max     5980.00   2855.00        29.00         29.00       30.00     90.00   

       plus_min left_coach_id right_coach_id referee_id left_num_v left_num_z  \
count  25848.00      25848.00       25848.00   25848.00   25848.00   25848.00   
mean       0.26      27577.34       26483.88    1450.75       0.98       3.84   
std        1.02      60441.67       58749.34    2577.68       0.17       1.04   
min        0.00         14.00          14.00       3.00       0.00       0.00   
25%        0.00       3953.00        3953.00     398.00       1.00       3.00   
50%        0.00       5135.00        4989.00     707.00       1.00       4.00   
75%        0.00      10386.00        8876.00    1137.00       1.00       4.00   
max       16.00     450457.00      450457.00   15584.00       2.00       8.00   

      left_num_p left_num_n left_num_u right_num_v right_num_z right_num_p  \
count   25848.00   25848.00   25848.00    25848.00    25848.00    25848.00   
mean        3.96       1.74       0.57        0.98        3.87        3.98   
std         1.35       0.94       1.12        0.17        1.07        1.33   
min         0.00       0.00       0.00        0.00        0.00        0.00   
25%         3.00       1.00       0.00        1.00        3.00        3.00   
50%         4.00       2.00       0.00        1.00        4.00        4.00   
75%         5.00       2.00       1.00        1.00        5.00        5.00   
max         9.00       6.00      10.00        2.00        8.00        9.00   

      right_num_n right_num_u left_num_y left_num_y2r right_num_y  \
count    25848.00    25848.00   25848.00     25848.00    25848.00   
mean         1.67        0.58       1.27         0.06        1.46   
std          0.93        1.11       1.19         0.24        1.27   
min          0.00        0.00       0.00         0.00        0.00   
25%          1.00        0.00       0.00         0.00        0.00   
50%          2.00        0.00       1.00         0.00        1.00   
75%          2.00        1.00       2.00         0.00        2.00   
max          5.00        9.00       9.00         2.00        8.00   

      right_num_y2r right_num_goal_g right_num_goal_p right_num_goal_a  \
count      25848.00         25848.00         25848.00         25848.00   
mean           0.08             0.65             0.07             0.02   
std            0.29             0.86             0.27             0.13   
min            0.00             0.00             0.00             0.00   
25%            0.00             0.00             0.00             0.00   
50%            0.00             0.00             0.00             0.00   
75%            0.00             1.00             0.00             0.00   
max            3.00             7.00             3.00             1.00   

      left_num_goal_g left_num_goal_p left_num_goal_a  \
count        25848.00        25848.00        25848.00   
mean             0.81            0.11            0.03   
std              0.98            0.33            0.17   
min              0.00            0.00            0.00   
25%              0.00            0.00            0.00   
50%              1.00            0.00            0.00   
75%              1.00            0.00            0.00   
max              8.00            3.00            1.00   

      left_total_transfer_value right_total_transfer_value  \
count